In [1]:
!pip install diffusers transformers torch sentencepiece protobuf peft accelerate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.1/44.1 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.5/40.5 kB 14.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.7/57.7 kB 21.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 149.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.1/10.1 MB 151.2 MB/s eta 0:00:00 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 157.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 319.7/319.7 kB 98.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 374.8/374.8 kB 102.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 336.4/336.4 kB 102.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 450.7/450.7 kB 112.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.9/183.9 kB 71.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 781.7/781.7 kB 144.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━

In [2]:
!huggingface-cli login --token ...

The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: fineGrained).
The token `nectar` has been saved to /root/.cache/huggingface/stored_tokens
Your token has been saved to /root/.cache/huggingface/token
Login successful.
The current active token is: `nectar`


In [3]:
import os
from PIL import Image
from datetime import datetime
from tqdm.auto import tqdm

def generate_filename(base_name, extension=".png"):
    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
    return f"{base_name}_{timestamp}{extension}"

def save_image(image, directory, base_name="image_grid"):
    filename = generate_filename(base_name)
    file_path = os.path.join(directory, filename)
    image.save(file_path)
    print(f"Image saved as {file_path}")

def image_grid(imgs, rows, cols, save=True, save_dir='generated_images', base_name="image_grid"):
    if not os.path.exists(save_dir):
        os.makedirs(save_dir)
    
    # Adjust rows and cols if the image count doesn't match
    total_images = len(imgs)
    expected_images = rows * cols
    if total_images != expected_images:
        print(f"Warning: Expected {expected_images} images, but got {total_images}. Adjusting grid size.")
        cols = min(total_images, cols)
        rows = (total_images + cols - 1) // cols  # Ensure all images fit in the grid

    w, h = imgs[0].size
    grid = Image.new('RGB', size=(cols * w, rows * h))

    for i, img in enumerate(imgs):
        grid.paste(img, box=(i % cols * w, i // cols * h))

    if save and save_dir:
        save_image(grid, save_dir, base_name)

    return grid


def download_image(url):
    try:
        response = requests.get(url)
    except:
        return None
    return Image.open(BytesIO(response.content)).convert("RGB")


In [5]:
# import torch
# from diffusers import FluxPipeline

# pipe = FluxPipeline.from_pretrained("black-forest-labs/FLUX.1-dev", cache_dir=".", torch_dtype=torch.bfloat16, force_download=True).to("cuda")

model_index.json:   0%|          | 0.00/536 [00:00<?, ?B/s]

Fetching 23 files:   0%|          | 0/23 [00:00<?, ?it/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

You set `add_prefix_space`. The tokenizer needs to be converted from the slow tokenizers


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [4]:
import torch
from diffusers import FluxPipeline

flux_dev_pipe = FluxPipeline.from_pretrained("black-forest-labs/FLUX.1-dev", cache_dir=".", torch_dtype=torch.bfloat16, force_download=True).to("cuda")

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

model_index.json:   0%|          | 0.00/536 [00:00<?, ?B/s]

Fetching 23 files:   0%|          | 0/23 [00:00<?, ?it/s]

tokenizer/merges.txt:   0%|          | 0.00/525k [00:00<?, ?B/s]

...

vae/config.json:   0%|          | 0.00/820 [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/168M [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

You set `add_prefix_space`. The tokenizer needs to be converted from the slow tokenizers


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

### 2500 steps

In [5]:
lora_path = "/workspace/taylor-rank16-multi-1e-4-constant/checkpoint-2500/pytorch_lora_weights.safetensors"
flux_dev_pipe.load_lora_weights(lora_path)
flux_dev_pipe.to("cuda")

FluxPipeline {
  "_class_name": "FluxPipeline",
  "_diffusers_version": "0.32.1",
  "_name_or_path": "black-forest-labs/FLUX.1-dev",
  "feature_extractor": [
    null,
    null
  ],
  "image_encoder": [
    null,
    null
  ],
  "scheduler": [
    "diffusers",
    "FlowMatchEulerDiscreteScheduler"
  ],
  "text_encoder": [
    "transformers",
    "CLIPTextModel"
  ],
  "text_encoder_2": [
    "transformers",
    "T5EncoderModel"
  ],
  "tokenizer": [
    "transformers",
    "CLIPTokenizer"
  ],
  "tokenizer_2": [
    "transformers",
    "T5TokenizerFast"
  ],
  "transformer": [
    "diffusers",
    "FluxTransformer2DModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ]
}

In [6]:
prompts = [
    "Close up photo of rwx woman wearing an exquisite white lace dress with intricate floral patterns, a delicate silver necklace, and pearl earrings. Her makeup is minimal, with a natural glow accentuating her features. The studio backdrop is a soft beige gradient, with professional lighting creating gentle shadows and highlights. Her expression is calm and poised, exuding timeless elegance.",
    "Close up photo of rwx woman wearing a sleek black leather jacket over a white turtleneck sweater. Her hair is styled in a modern bob, and she has a piercing gaze that conveys confidence. The backdrop is an urban skyline at dusk, with golden light reflecting off glass buildings. Subtle HDR lighting enhances the depth of her features.",
    "Close up photo of rwx woman in a luxurious evening gown of deep crimson velvet, her hair styled into soft waves cascading over one shoulder. She wears diamond earrings and a matching necklace. The backdrop is a dimly lit grand ballroom, with golden chandeliers casting a warm glow. Her expression is one of quiet sophistication.",
    "Close up photo of rwx woman with her hair tied into a tight, elegant bun, wearing a high-tech metallic silver suit with glowing blue lines integrated into the design. The futuristic backdrop features holographic screens and neon lights. Her intense expression suggests intelligence and focus.",
    "Medium shot photo of rwx woman wearing a traditional sari in vibrant shades of gold and red, with intricate embroidery. She has a delicate bindi on her forehead, and her jewelry includes gold jhumkas and a necklace with emerald accents. The backdrop is a palace courtyard at sunset, with warm orange hues highlighting her serene expression.",
    "Medium shot photo of rwx woman dressed in a rugged explorer outfit: a khaki shirt with rolled-up sleeves, a leather hat, and a bandana around her neck. Her expression is determined, with a hint of adventure. The backdrop is a dense jungle, with sunlight streaming through the leaves.",
    "Medium shot photo of rwx woman in a glowing elven robe of silver and white, her ears subtly pointed, and a delicate circlet of intertwined gold leaves adorning her head. The magical forest backdrop features luminous plants and a soft mist illuminated by moonlight. Her expression is wise and ethereal.",
    "Full shot photo of rwx woman wearing an elaborate black and gold masquerade mask, her gown shimmering with sequins that catch the light. Her lips are painted a deep red, and her eyes peer through the mask with a mysterious allure. The backdrop is a Venetian-style ballroom filled with masked figures.",
    "Full shot photo of rwx woman in a tailored white blazer over a silk blouse, her hair in a polished low bun. Her accessories include minimalist gold hoop earrings and a smartwatch. The backdrop is a modern corporate office with floor-to-ceiling windows overlooking a bustling cityscape.",
    "Full shot photo of rwx woman with flowing red hair adorned with wildflowers, wearing a simple yet elegant white linen dress. Her expression is serene, and her freckles are highlighted by the golden hour light. The backdrop is a lush meadow with tall grass swaying in the gentle breeze."
]

save_dir = "taylor_lora_2500steps_generated_images"
for i, prompt in enumerate(prompts):
    print(f"Generating images for prompt {i+1}/{len(prompts)}: {prompt}")
    images = flux_dev_pipe(prompt, 
                  num_inference_steps=35, 
                  num_images_per_prompt=1, 
                  width=1024,
                  height=1024,
                  guidance_scale=3.5,
                  generator=torch.Generator("cpu").manual_seed(1024)).images

    if not os.path.exists(save_dir):
        os.makedirs(save_dir)
        
    images[0].save(f"{save_dir}/prompt_{i+1}.jpg")

Generating images for prompt 1/10: Close up photo of rwx woman wearing an exquisite white lace dress with intricate floral patterns, a delicate silver necklace, and pearl earrings. Her makeup is minimal, with a natural glow accentuating her features. The studio backdrop is a soft beige gradient, with professional lighting creating gentle shadows and highlights. Her expression is calm and poised, exuding timeless elegance.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 2/10: Close up photo of rwx woman wearing a sleek black leather jacket over a white turtleneck sweater. Her hair is styled in a modern bob, and she has a piercing gaze that conveys confidence. The backdrop is an urban skyline at dusk, with golden light reflecting off glass buildings. Subtle HDR lighting enhances the depth of her features.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 3/10: Close up photo of rwx woman in a luxurious evening gown of deep crimson velvet, her hair styled into soft waves cascading over one shoulder. She wears diamond earrings and a matching necklace. The backdrop is a dimly lit grand ballroom, with golden chandeliers casting a warm glow. Her expression is one of quiet sophistication.


...

  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 9/10: Full shot photo of rwx woman in a tailored white blazer over a silk blouse, her hair in a polished low bun. Her accessories include minimalist gold hoop earrings and a smartwatch. The backdrop is a modern corporate office with floor-to-ceiling windows overlooking a bustling cityscape.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 10/10: Full shot photo of rwx woman with flowing red hair adorned with wildflowers, wearing a simple yet elegant white linen dress. Her expression is serene, and her freckles are highlighted by the golden hour light. The backdrop is a lush meadow with tall grass swaying in the gentle breeze.


  0%|          | 0/35 [00:00<?, ?it/s]

### 2000 steps

In [7]:
flux_dev_pipe.fuse_lora(lora_scale=0)

In [8]:
lora_path = "/workspace/taylor-rank16-multi-1e-4-constant/checkpoint-2000/pytorch_lora_weights.safetensors"
flux_dev_pipe.load_lora_weights(lora_path)
flux_dev_pipe.to("cuda")

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/model.py:431: UserWarning: Adapter cannot be set when the model is merged. Unmerging the model first.
  warnings.warn("Adapter cannot be set when the model is merged. Unmerging the model first.")


FluxPipeline {
  "_class_name": "FluxPipeline",
  "_diffusers_version": "0.32.1",
  "_name_or_path": "black-forest-labs/FLUX.1-dev",
  "feature_extractor": [
    null,
    null
  ],
  "image_encoder": [
    null,
    null
  ],
  "scheduler": [
    "diffusers",
    "FlowMatchEulerDiscreteScheduler"
  ],
  "text_encoder": [
    "transformers",
    "CLIPTextModel"
  ],
  "text_encoder_2": [
    "transformers",
    "T5EncoderModel"
  ],
  "tokenizer": [
    "transformers",
    "CLIPTokenizer"
  ],
  "tokenizer_2": [
    "transformers",
    "T5TokenizerFast"
  ],
  "transformer": [
    "diffusers",
    "FluxTransformer2DModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ]
}

In [9]:
prompts = [
    "Close up photo of ext woman wearing an exquisite white lace dress with intricate floral patterns, a delicate silver necklace, and pearl earrings. Her makeup is minimal, with a natural glow accentuating her features. The studio backdrop is a soft beige gradient, with professional lighting creating gentle shadows and highlights. Her expression is calm and poised, exuding timeless elegance.",
    "Close up photo of ext woman wearing a sleek black leather jacket over a white turtleneck sweater. Her hair is styled in a modern bob, and she has a piercing gaze that conveys confidence. The backdrop is an urban skyline at dusk, with golden light reflecting off glass buildings. Subtle HDR lighting enhances the depth of her features.",
    "Close up photo of ext woman in a luxurious evening gown of deep crimson velvet, her hair styled into soft waves cascading over one shoulder. She wears diamond earrings and a matching necklace. The backdrop is a dimly lit grand ballroom, with golden chandeliers casting a warm glow. Her expression is one of quiet sophistication.",
    "Close up photo of ext woman with her hair tied into a tight, elegant bun, wearing a high-tech metallic silver suit with glowing blue lines integrated into the design. The futuristic backdrop features holographic screens and neon lights. Her intense expression suggests intelligence and focus.",
    "Medium shot photo of ext woman wearing a traditional sari in vibrant shades of gold and red, with intricate embroidery. She has a delicate bindi on her forehead, and her jewelry includes gold jhumkas and a necklace with emerald accents. The backdrop is a palace courtyard at sunset, with warm orange hues highlighting her serene expression.",
    "Medium shot photo of ext woman dressed in a rugged explorer outfit: a khaki shirt with rolled-up sleeves, a leather hat, and a bandana around her neck. Her expression is determined, with a hint of adventure. The backdrop is a dense jungle, with sunlight streaming through the leaves.",
    "Medium shot photo of ext woman in a glowing elven robe of silver and white, her ears subtly pointed, and a delicate circlet of intertwined gold leaves adorning her head. The magical forest backdrop features luminous plants and a soft mist illuminated by moonlight. Her expression is wise and ethereal.",
    "Full shot photo of ext woman wearing an elaborate black and gold masquerade mask, her gown shimmering with sequins that catch the light. Her lips are painted a deep red, and her eyes peer through the mask with a mysterious allure. The backdrop is a Venetian-style ballroom filled with masked figures.",
    "Full shot photo of ext woman in a tailored white blazer over a silk blouse, her hair in a polished low bun. Her accessories include minimalist gold hoop earrings and a smartwatch. The backdrop is a modern corporate office with floor-to-ceiling windows overlooking a bustling cityscape.",
    "Full shot photo of ext woman with flowing red hair adorned with wildflowers, wearing a simple yet elegant white linen dress. Her expression is serene, and her freckles are highlighted by the golden hour light. The backdrop is a lush meadow with tall grass swaying in the gentle breeze."
]

save_dir = "lora_2000steps_generated_images"
for i, prompt in enumerate(prompts):
    print(f"Generating images for prompt {i+1}/{len(prompts)}: {prompt}")
    images = flux_dev_pipe(prompt, 
                  num_inference_steps=35, 
                  num_images_per_prompt=1, 
                  width=1024,
                  height=1024,
                  guidance_scale=3.5,
                  generator=torch.Generator("cpu").manual_seed(1024)).images

    if not os.path.exists(save_dir):
        os.makedirs(save_dir)
               
    images[0].save(f"{save_dir}/prompt_{i+1}.jpg")

Generating images for prompt 1/10: Close up photo of ext woman wearing an exquisite white lace dress with intricate floral patterns, a delicate silver necklace, and pearl earrings. Her makeup is minimal, with a natural glow accentuating her features. The studio backdrop is a soft beige gradient, with professional lighting creating gentle shadows and highlights. Her expression is calm and poised, exuding timeless elegance.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 2/10: Close up photo of ext woman wearing a sleek black leather jacket over a white turtleneck sweater. Her hair is styled in a modern bob, and she has a piercing gaze that conveys confidence. The backdrop is an urban skyline at dusk, with golden light reflecting off glass buildings. Subtle HDR lighting enhances the depth of her features.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 3/10: Close up photo of ext woman in a luxurious evening gown of deep crimson velvet, her hair styled into soft waves cascading over one shoulder. She wears diamond earrings and a matching necklace. The backdrop is a dimly lit grand ballroom, with golden chandeliers casting a warm glow. Her expression is one of quiet sophistication.


...

  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 9/10: Full shot photo of ext woman in a tailored white blazer over a silk blouse, her hair in a polished low bun. Her accessories include minimalist gold hoop earrings and a smartwatch. The backdrop is a modern corporate office with floor-to-ceiling windows overlooking a bustling cityscape.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 10/10: Full shot photo of ext woman with flowing red hair adorned with wildflowers, wearing a simple yet elegant white linen dress. Her expression is serene, and her freckles are highlighted by the golden hour light. The backdrop is a lush meadow with tall grass swaying in the gentle breeze.


  0%|          | 0/35 [00:00<?, ?it/s]

### 1500 steps

In [10]:
flux_dev_pipe.fuse_lora(lora_scale=0)

In [11]:
lora_path = "/workspace/taylor-rank16-multi-1e-4-constant/checkpoint-1500/pytorch_lora_weights.safetensors"
flux_dev_pipe.load_lora_weights(lora_path)
flux_dev_pipe.to("cuda")

FluxPipeline {
  "_class_name": "FluxPipeline",
  "_diffusers_version": "0.32.1",
  "_name_or_path": "black-forest-labs/FLUX.1-dev",
  "feature_extractor": [
    null,
    null
  ],
  "image_encoder": [
    null,
    null
  ],
  "scheduler": [
    "diffusers",
    "FlowMatchEulerDiscreteScheduler"
  ],
  "text_encoder": [
    "transformers",
    "CLIPTextModel"
  ],
  "text_encoder_2": [
    "transformers",
    "T5EncoderModel"
  ],
  "tokenizer": [
    "transformers",
    "CLIPTokenizer"
  ],
  "tokenizer_2": [
    "transformers",
    "T5TokenizerFast"
  ],
  "transformer": [
    "diffusers",
    "FluxTransformer2DModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ]
}

In [12]:
prompts = [
    "Close up photo of ext woman wearing an exquisite white lace dress with intricate floral patterns, a delicate silver necklace, and pearl earrings. Her makeup is minimal, with a natural glow accentuating her features. The studio backdrop is a soft beige gradient, with professional lighting creating gentle shadows and highlights. Her expression is calm and poised, exuding timeless elegance.",
    "Close up photo of ext woman wearing a sleek black leather jacket over a white turtleneck sweater. Her hair is styled in a modern bob, and she has a piercing gaze that conveys confidence. The backdrop is an urban skyline at dusk, with golden light reflecting off glass buildings. Subtle HDR lighting enhances the depth of her features.",
    "Close up photo of ext woman in a luxurious evening gown of deep crimson velvet, her hair styled into soft waves cascading over one shoulder. She wears diamond earrings and a matching necklace. The backdrop is a dimly lit grand ballroom, with golden chandeliers casting a warm glow. Her expression is one of quiet sophistication.",
    "Close up photo of ext woman with her hair tied into a tight, elegant bun, wearing a high-tech metallic silver suit with glowing blue lines integrated into the design. The futuristic backdrop features holographic screens and neon lights. Her intense expression suggests intelligence and focus.",
    "Medium shot photo of ext woman wearing a traditional sari in vibrant shades of gold and red, with intricate embroidery. She has a delicate bindi on her forehead, and her jewelry includes gold jhumkas and a necklace with emerald accents. The backdrop is a palace courtyard at sunset, with warm orange hues highlighting her serene expression.",
    "Medium shot photo of ext woman dressed in a rugged explorer outfit: a khaki shirt with rolled-up sleeves, a leather hat, and a bandana around her neck. Her expression is determined, with a hint of adventure. The backdrop is a dense jungle, with sunlight streaming through the leaves.",
    "Medium shot photo of ext woman in a glowing elven robe of silver and white, her ears subtly pointed, and a delicate circlet of intertwined gold leaves adorning her head. The magical forest backdrop features luminous plants and a soft mist illuminated by moonlight. Her expression is wise and ethereal.",
    "Full shot photo of ext woman wearing an elaborate black and gold masquerade mask, her gown shimmering with sequins that catch the light. Her lips are painted a deep red, and her eyes peer through the mask with a mysterious allure. The backdrop is a Venetian-style ballroom filled with masked figures.",
    "Full shot photo of ext woman in a tailored white blazer over a silk blouse, her hair in a polished low bun. Her accessories include minimalist gold hoop earrings and a smartwatch. The backdrop is a modern corporate office with floor-to-ceiling windows overlooking a bustling cityscape.",
    "Full shot photo of ext woman with flowing red hair adorned with wildflowers, wearing a simple yet elegant white linen dress. Her expression is serene, and her freckles are highlighted by the golden hour light. The backdrop is a lush meadow with tall grass swaying in the gentle breeze."
]

save_dir = "taylor_lora_1500steps_generated_images"
for i, prompt in enumerate(prompts):
    print(f"Generating images for prompt {i+1}/{len(prompts)}: {prompt}")
    images = flux_dev_pipe(prompt, 
                  num_inference_steps=35, 
                  num_images_per_prompt=1, 
                  width=1024,
                  height=1024,
                  guidance_scale=3.5,
                  generator=torch.Generator("cpu").manual_seed(1024)).images

    if not os.path.exists(save_dir):
        os.makedirs(save_dir)
               
    images[0].save(f"{save_dir}/prompt_{i+1}.jpg")

Generating images for prompt 1/10: Close up photo of ext woman wearing an exquisite white lace dress with intricate floral patterns, a delicate silver necklace, and pearl earrings. Her makeup is minimal, with a natural glow accentuating her features. The studio backdrop is a soft beige gradient, with professional lighting creating gentle shadows and highlights. Her expression is calm and poised, exuding timeless elegance.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 2/10: Close up photo of ext woman wearing a sleek black leather jacket over a white turtleneck sweater. Her hair is styled in a modern bob, and she has a piercing gaze that conveys confidence. The backdrop is an urban skyline at dusk, with golden light reflecting off glass buildings. Subtle HDR lighting enhances the depth of her features.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 3/10: Close up photo of ext woman in a luxurious evening gown of deep crimson velvet, her hair styled into soft waves cascading over one shoulder. She wears diamond earrings and a matching necklace. The backdrop is a dimly lit grand ballroom, with golden chandeliers casting a warm glow. Her expression is one of quiet sophistication.


...

  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 9/10: Full shot photo of ext woman in a tailored white blazer over a silk blouse, her hair in a polished low bun. Her accessories include minimalist gold hoop earrings and a smartwatch. The backdrop is a modern corporate office with floor-to-ceiling windows overlooking a bustling cityscape.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 10/10: Full shot photo of ext woman with flowing red hair adorned with wildflowers, wearing a simple yet elegant white linen dress. Her expression is serene, and her freckles are highlighted by the golden hour light. The backdrop is a lush meadow with tall grass swaying in the gentle breeze.


  0%|          | 0/35 [00:00<?, ?it/s]

### Final steps

In [13]:
flux_dev_pipe.fuse_lora(lora_scale=0)

In [15]:
lora_path = "/workspace/taylor-rank16-multi-1e-4-constant/pytorch_lora_weights.safetensors"
flux_dev_pipe.load_lora_weights(lora_path)
flux_dev_pipe.to("cuda")

FluxPipeline {
  "_class_name": "FluxPipeline",
  "_diffusers_version": "0.32.1",
  "_name_or_path": "black-forest-labs/FLUX.1-dev",
  "feature_extractor": [
    null,
    null
  ],
  "image_encoder": [
    null,
    null
  ],
  "scheduler": [
    "diffusers",
    "FlowMatchEulerDiscreteScheduler"
  ],
  "text_encoder": [
    "transformers",
    "CLIPTextModel"
  ],
  "text_encoder_2": [
    "transformers",
    "T5EncoderModel"
  ],
  "tokenizer": [
    "transformers",
    "CLIPTokenizer"
  ],
  "tokenizer_2": [
    "transformers",
    "T5TokenizerFast"
  ],
  "transformer": [
    "diffusers",
    "FluxTransformer2DModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ]
}

In [16]:
prompts = [
    "Close up photo of ext woman wearing an exquisite white lace dress with intricate floral patterns, a delicate silver necklace, and pearl earrings. Her makeup is minimal, with a natural glow accentuating her features. The studio backdrop is a soft beige gradient, with professional lighting creating gentle shadows and highlights. Her expression is calm and poised, exuding timeless elegance.",
    "Close up photo of ext woman wearing a sleek black leather jacket over a white turtleneck sweater. Her hair is styled in a modern bob, and she has a piercing gaze that conveys confidence. The backdrop is an urban skyline at dusk, with golden light reflecting off glass buildings. Subtle HDR lighting enhances the depth of her features.",
    "Close up photo of ext woman in a luxurious evening gown of deep crimson velvet, her hair styled into soft waves cascading over one shoulder. She wears diamond earrings and a matching necklace. The backdrop is a dimly lit grand ballroom, with golden chandeliers casting a warm glow. Her expression is one of quiet sophistication.",
    "Close up photo of ext woman with her hair tied into a tight, elegant bun, wearing a high-tech metallic silver suit with glowing blue lines integrated into the design. The futuristic backdrop features holographic screens and neon lights. Her intense expression suggests intelligence and focus.",
    "Medium shot photo of ext woman wearing a traditional sari in vibrant shades of gold and red, with intricate embroidery. She has a delicate bindi on her forehead, and her jewelry includes gold jhumkas and a necklace with emerald accents. The backdrop is a palace courtyard at sunset, with warm orange hues highlighting her serene expression.",
    "Medium shot photo of ext woman dressed in a rugged explorer outfit: a khaki shirt with rolled-up sleeves, a leather hat, and a bandana around her neck. Her expression is determined, with a hint of adventure. The backdrop is a dense jungle, with sunlight streaming through the leaves.",
    "Medium shot photo of ext woman in a glowing elven robe of silver and white, her ears subtly pointed, and a delicate circlet of intertwined gold leaves adorning her head. The magical forest backdrop features luminous plants and a soft mist illuminated by moonlight. Her expression is wise and ethereal.",
    "Full shot photo of ext woman wearing an elaborate black and gold masquerade mask, her gown shimmering with sequins that catch the light. Her lips are painted a deep red, and her eyes peer through the mask with a mysterious allure. The backdrop is a Venetian-style ballroom filled with masked figures.",
    "Full shot photo of ext woman in a tailored white blazer over a silk blouse, her hair in a polished low bun. Her accessories include minimalist gold hoop earrings and a smartwatch. The backdrop is a modern corporate office with floor-to-ceiling windows overlooking a bustling cityscape.",
    "Full shot photo of ext woman with flowing red hair adorned with wildflowers, wearing a simple yet elegant white linen dress. Her expression is serene, and her freckles are highlighted by the golden hour light. The backdrop is a lush meadow with tall grass swaying in the gentle breeze."
]

negative_prompt = "(old,wrinkles,deformed iris, deformed pupils, semi-realistic, cgi, 3d, render, sketch, cartoon, drawing, anime), text, cropped, out of frame, worst quality, low quality, jpeg artifacts, ugly, duplicate, morbid, mutilated, extra fingers, mutated hands, poorly drawn hands, poorly drawn face, mutation, deformed, blurry, dehydrated, bad anatomy, bad proportions, extra limbs, cloned face, disfigured, gross proportions, malformed limbs, missing arms, missing legs, extra arms, extra legs, fused fingers, too many fingers, long neck"

save_dir = "taylor_lora_finalsteps_generated_images"
for i, prompt in enumerate(prompts):
    print(f"Generating images for prompt {i+1}/{len(prompts)}: {prompt}")
    images = flux_dev_pipe(prompt, 
                           negative_prompt=negative_prompt,
                           num_inference_steps=35, 
                           num_images_per_prompt=1, 
                           width=1024,
                           height=1024,
                           guidance_scale=3.5,
                           generator=torch.Generator("cpu").manual_seed(1024)
                          ).images

    if not os.path.exists(save_dir):
        os.makedirs(save_dir)
               
    images[0].save(f"{save_dir}/prompt_{i+1}.jpg")

Generating images for prompt 1/10: Close up photo of ext woman wearing an exquisite white lace dress with intricate floral patterns, a delicate silver necklace, and pearl earrings. Her makeup is minimal, with a natural glow accentuating her features. The studio backdrop is a soft beige gradient, with professional lighting creating gentle shadows and highlights. Her expression is calm and poised, exuding timeless elegance.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 2/10: Close up photo of ext woman wearing a sleek black leather jacket over a white turtleneck sweater. Her hair is styled in a modern bob, and she has a piercing gaze that conveys confidence. The backdrop is an urban skyline at dusk, with golden light reflecting off glass buildings. Subtle HDR lighting enhances the depth of her features.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 3/10: Close up photo of ext woman in a luxurious evening gown of deep crimson velvet, her hair styled into soft waves cascading over one shoulder. She wears diamond earrings and a matching necklace. The backdrop is a dimly lit grand ballroom, with golden chandeliers casting a warm glow. Her expression is one of quiet sophistication.


...

  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 9/10: Full shot photo of ext woman in a tailored white blazer over a silk blouse, her hair in a polished low bun. Her accessories include minimalist gold hoop earrings and a smartwatch. The backdrop is a modern corporate office with floor-to-ceiling windows overlooking a bustling cityscape.


  0%|          | 0/35 [00:00<?, ?it/s]

Generating images for prompt 10/10: Full shot photo of ext woman with flowing red hair adorned with wildflowers, wearing a simple yet elegant white linen dress. Her expression is serene, and her freckles are highlighted by the golden hour light. The backdrop is a lush meadow with tall grass swaying in the gentle breeze.


  0%|          | 0/35 [00:00<?, ?it/s]